# Analysis Template
WIP new analysis template. Only to be used with most recent version of kinetics package as of 11/21/23.

In [172]:
#MISSING PACKAGES: plotly, dash, pint

In [173]:
### PARAMETERS:
EGFP_SLOPE = 91900.03
EGFP_SLOPE_CONC_UNITS = 'nM' #RFU/nM


In [174]:
#enables autoreloding of modules
%load_ext autoreload
%autoreload 2

from copy import deepcopy
from pathlib import Path

import skimage
import math
import numpy as np
import pandas as pd
import scipy.stats
from pprint import pprint
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from scipy.optimize import curve_fit

from pathlib import Path 
#from htbam_analysis.htbam_db_api import LocalHtbamDBAPI
#temporary, fix soon:
#import sys
#sys.path.append('../../htbam_db_api/src/htbam_db_api')
from htbam_db_api.htbam_db_api import HTBAM_Experiment
#Import Kinetics Package for line fitting:
#import sys
#sys.path.append('../../kinetic_analysis/')
import kinetics
from kinetics.chip import analysis, visualization

#Configuration settings for pandas and seaborn
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.float_format', '{:.2f}'.format)
#sns.set(style='ticks', context='paper', font_scale=1.2, rc={"lines.linewidth": 1.2})

#enable inline plotting of matplotlib figures
%matplotlib inline

#set the figure format to SVG
%config InlineBackend.figure_format = 'svg'


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## 1. Connect DB Api

In [175]:
#TODO: add proper file path parsing

root = '../local_test_data/'
root = Path(root)
db = HTBAM_Experiment('test_exp.HTBAM', new=True)
print(db.get(''))

#load standards, kinetics, and button quant:
db.load_standard_data_from_file(
    standard_curve_data_path= root/'d1_NADPH_StandardSeries_Analysis.csv.bz2', 
    standard_name="NADPH std curve", 
    standard_type="NADPH", 
    standard_units="uM",)
db.load_kinetics_data_from_file(
    kinetic_data_path= root/'d1_TitrationSeries_Analysis.csv', 
    kinetic_name="NADPH kinetics curve", 
    kinetic_type="NADPH", 
    kinetic_units="uM")
db.load_button_quant_data_from_file(root / 'd1_TitrationSeries_Analysis.csv.bz2')

### TODO: Still want the following data in the database:
# date (and time?) collected
# operator name
# Add additional descriptors
# substrate_name
# setup(?) and device_num
# width/height


{'file_version': '0.0.1', 'chamber_metadata': {}, 'button_quant': {}, 'runs': {}}


#### Format of DB:
Useful? Or remove?
DB
- **chamber_metadata**
    - '1,1'
        - 'id'                  'organism_ADK'
        - 'radius_chamber'      35.0
        - 'x_center_chamber'    31.0
        - 'y_center_chamber'    43.0
        - 'xslice'              '(6758, 6805)'
        - 'yslice'              '(6704, 6804)'
    - ...
    - '32,56' ...
- **runs**
    - 'standard_0'
        - 'name'            'NAPDH_std_curve'
        - 'type'            'NAPDH'
        - 'conc_unit'       'uM'
        - 'assays':
            - 0:
                - 'conc'
                - 'time_s'
                - 'chambers'
                    - '1,1'
                    - ...
                    - '32,56' ...
            - ...
            - 6: ...
        - 'analyses':
            - 'linear_regression':
                - 'chambers':
                    - '1,1':
                        - slope:
                        - intercept:
                        - r_value:
                        - p_value: 
                        - std_err:
                    - ...
                    - '32,56'...


## 2. Standards

For each chamber, we've taken values at a set of concentrations. We need to perform a linear regression __for each chamber__ to relate the luminance of each chamber to its substrate concentration.

In our hierarchical data structure, we will store this linear regression as an analysis under the standard curve experiment. It is stored under:

```db_conn._json_dict['runs']['standard_0']['analyses']['linear_regression']```

And it stores the data:
```
{'chambers':  {'1,1': 
                     {'intercept': ...,
                      'p_value': ...,
                      'r2': ...,
                      'r_value': ...,
                      'slope': ...,
                      'std_err': ...,
                     }
               '1,2': {'intercept': ...}
              }
}
```


In [176]:
#let's automatigically generate the standard curve by doing a linear regression:
kinetics.chip.analysis.new_analysis(db, 'standard_0', 'linear_regression', 'linear_regression')

In [177]:
db.get('runs/standard_0/analyses/linear_regression')

{'chambers': {'1,1': {'slope': {'values': 130682.53156610447,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1241165.4969627894,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995400721869304,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.999080355907454,
    'unit': 'dimensionless',
    'is_quantity': True},
   'p_value': {'values': 8.711060082554288e-09,
    'unit': 'dimensionless',
    'is_quantity': True},
   'std_err': {'values': 1773.1367031323791,
    'unit': 'RFU',
    'is_quantity': True}},
  '1,2': {'slope': {'values': 140364.61222647715,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1280247.3718265183,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995837661823704,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.9991677056153319,
    'unit': 'dimensionless',
    'is_quantity': True},
   

### Sanity check:
Now, let's sanity check by plotting. We can use the ```plot_chip()``` function to show a chip where each chamber is colored by variable (like luminance). We can also make subplots on hover.

In [178]:
from kinetics.chip import visualization

In [179]:
db.get('runs/standard_0/analyses/linear_regression')

{'chambers': {'1,1': {'slope': {'values': 130682.53156610447,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1241165.4969627894,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995400721869304,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.999080355907454,
    'unit': 'dimensionless',
    'is_quantity': True},
   'p_value': {'values': 8.711060082554288e-09,
    'unit': 'dimensionless',
    'is_quantity': True},
   'std_err': {'values': 1773.1367031323791,
    'unit': 'RFU',
    'is_quantity': True}},
  '1,2': {'slope': {'values': 140364.61222647715,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1280247.3718265183,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995837661823704,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.9991677056153319,
    'unit': 'dimensionless',
    'is_quantity': True},
   

In [180]:
kinetics.chip.visualization.plot(db, 'standard_0', 'linear_regression', 'r2', title='Standard Curve')

/home/nfreitas/miniconda3/envs/analysis_test_2/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:201: UnitStrippedWarning:

The unit of the quantity is stripped when downcasting to ndarray.

/home/nfreitas/miniconda3/envs/analysis_test_2/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:129: UnitStrippedWarning:

The unit of the quantity is stripped when downcasting to ndarray.



## 7. Fit initial rates from processed kinetic data

For this next part, we'll be generating the predicted product concentration for each well, for each time, and for each substrate concentration. That's a 3D array.

To do this, we divide our luminance value (in RFUs) by the slope of the chamber's standard curve (RFU/conc). Here, we ignore the standard curve intercept.

In [183]:
chamber_idxs, luminance_data, conc_data, time_data = db.get_run_data('kinetics_0')
print('Luminance data shape:', luminance_data.shape) #(time x wells x assays)


Luminance data shape: (23, 1792, 11)


Each well contains time_series data. We have 32*56 wells (1792), and then N assays with different concentrations.
So we have a np array with dimensions (time x wells x assays)
For a standard, this will be (1, 1792, # concentrations)
For a kinetics run, this will be (~20, 1792, # concentrations)

In [184]:
db.get(f'runs/standard_0/analyses/linear_regression')

{'chambers': {'1,1': {'slope': {'values': 130682.53156610447,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1241165.4969627894,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995400721869304,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.999080355907454,
    'unit': 'dimensionless',
    'is_quantity': True},
   'p_value': {'values': 8.711060082554288e-09,
    'unit': 'dimensionless',
    'is_quantity': True},
   'std_err': {'values': 1773.1367031323791,
    'unit': 'RFU',
    'is_quantity': True}},
  '1,2': {'slope': {'values': 140364.61222647715,
    'unit': 'RFU / micromolar',
    'is_quantity': True},
   'intercept': {'values': -1280247.3718265183,
    'unit': 'RFU',
    'is_quantity': True},
   'r_value': {'values': 0.9995837661823704,
    'unit': 'dimensionless',
    'is_quantity': True},
   'r2': {'values': 0.9991677056153319,
    'unit': 'dimensionless',
    'is_quantity': True},
   

In [186]:
chamber_dict = db.get(f'runs/standard_0/analyses/linear_regression/chambers/')
chamber_dict = db._make_quantities_from_serialized_dict(chamber_dict)

#concatenate all the slope quantities:
slope_quantities = [chamber_dict[i]['slope'] for i in chamber_dict.keys()]
# Assuming `slope_quantities` is the list of quantities
slope_array = np.array([q.magnitude for q in slope_quantities]) * slope_quantities[0].units
print('Slope quantities:', slope_array)



Slope quantities: [130682.53156610447 140364.61222647715 143138.28541644535 ... 142844.24842387513 138054.28130525304 133308.7650239111] RFU / micromolar


In [189]:
luminance_data / slope_array[np.newaxis, :, np.newaxis]

array([[[0.00000000e+00, 2.73525463e-01, 2.05612791e-02, ...,
         8.89139494e-01, 9.51884682e+00, 3.44901644e+01],
        [0.00000000e+00, 3.27048244e-01, 4.41421802e-02, ...,
         9.23779847e-01, 9.65082280e+00, 3.60615466e+01],
        [0.00000000e+00, 4.33273319e-01, 4.87291012e-02, ...,
         1.09868579e+00, 1.00476053e+01, 3.64474814e+01],
        ...,
        [0.00000000e+00, 8.07693703e+00, 4.06036649e-04, ...,
         2.68824264e-02, 3.73742734e-01, 5.98722041e-01],
        [0.00000000e+00, 5.07364200e+00, 3.89701786e-03, ...,
         2.82280271e-02, 3.92374648e-01, 5.83408202e-01],
        [0.00000000e+00, 2.51504093e+00, 0.00000000e+00, ...,
         6.72573930e-02, 4.81071143e-01, 6.96083262e-01]],

       [[7.99869721e-01, 7.39961178e-02, 1.06517679e-02, ...,
         2.00722925e+01, 3.24188164e+01, 5.82595234e+01],
        [8.33465060e-01, 8.25635452e-02, 9.96689962e-03, ...,
         5.51941111e-01, 7.98901505e+00, 3.32165845e+01],
        [1.04042744e+00, 1.30810565e-01, 2.05605369e-02, ...,
         5.21749298e+00, 1.60275708e+01, 4.22236020e+01],
        ...,
        [2.65309247e+00, 7.77039336e+00, 0.00000000e+00, ...,
         4.90744295e-02, 3.59132416e-01, 6.50680731e-01],
        [2.62950194e+00, 5.03671450e+00, 0.00000000e+00, ...,
         3.31246518e-02, 3.86304572e-01, 6.55350918e-01],
        [3.15016796e+00, 2.72245415e+00, 0.00000000e+00, ...,
         2.62248322e-01, 7.76873148e-01, 1.19037934e+00]],

       [[4.53993348e-01, 5.16978047e-02, 1.12562864e-02, ...,
         5.34431796e+01, 7.09208636e+01, 1.00259636e+02],
        [5.02840416e-01, 5.49354989e-02, 8.94100001e-03, ...,
         4.13266557e-01, 7.42838942e+00, 3.22426210e+01],
        [6.01725805e-01, 8.10125674e-02, 1.50553711e-02, ...,
         1.59232311e+01, 2.88786469e+01, 5.51958547e+01],
        ...,
        [3.12990551e+00, 7.95814331e+00, 5.67751246e-03, ...,
         3.65432984e-02, 3.89088119e-01, 6.77724172e-01],
        [3.07983929e+00, 5.10582499e+00, 0.00000000e+00, ...,
         4.92704749e-02, 4.07875797e-01, 7.13299139e-01],
        [4.18738408e+00, 3.16226019e+00, 0.00000000e+00, ...,
         5.15780039e-01, 1.22346044e+00, 1.88054401e+00]],

       ...,

       [[8.82290836e-02, 8.63619633e-02, 1.43837128e+00, ...,
         4.67267295e+02, 5.98170766e+02, 6.46760680e+02],
        [3.49304566e-02, 1.88081594e-03, 8.19294822e-04, ...,
         4.33807347e+00, 1.47736667e+01, 4.14167425e+01],
        [1.44964710e-01, 9.63404023e-02, 9.66464001e-01, ...,
         2.80962992e+02, 3.37213275e+02, 3.91274989e+02],
        ...,
        [2.37393667e+01, 1.43743624e+01, 0.00000000e+00, ...,
         4.96274794e-01, 1.17874539e+00, 1.70249767e+00],
        [2.34641981e+01, 1.06511510e+01, 0.00000000e+00, ...,
         7.47785574e-01, 1.61290905e+00, 2.47614921e+00],
        [3.75487463e+01, 1.59116919e+01, 0.00000000e+00, ...,
         1.20427723e+02, 1.73717310e+02, 2.16804754e+02]],

       [[1.63395978e-01, 1.97968311e-01, 1.97779303e+00, ...,
         5.07574541e+02, 6.45588924e+02, 6.65269696e+02],
        [6.81653292e-02, 1.02589960e-02, 0.00000000e+00, ...,
         6.04368143e+00, 1.83582525e+01, 4.57077457e+01],
        [2.10900947e-01, 2.17097752e-01, 1.56072150e+00, ...,
         3.15759714e+02, 3.84652456e+02, 4.45732418e+02],
        ...,
        [2.89407172e+01, 1.75549665e+01, 0.00000000e+00, ...,
         6.49889660e-01, 1.41767696e+00, 2.12742202e+00],
        [2.84761542e+01, 1.37638180e+01, 0.00000000e+00, ...,
         9.51951644e-01, 2.04283415e+00, 3.26831588e+00],
        [4.32091243e+01, 1.98180067e+01, 0.00000000e+00, ...,
         1.44489074e+02, 2.03546939e+02, 2.50039905e+02]],

       [[2.43207716e-01, 3.05871026e-01, 2.45048054e+00, ...,
         5.61846538e+02, 6.86477649e+02, 6.76560883e+02],
        [7.83388336e-02, 5.72793945e-03, 1.50322789e-03, ...,
         9.36473217e+00, 2.21416492e+01, 4.99993260e+01],
        [3.01498651e-01, 3.79262612e-01, 2.02673938e+00, ...,
         3

In [9]:
slopes = np.array([db_conn._json_dict['runs']['standard_0']['analyses']['linear_regression']['chambers'][chamber_idx]['slope'] for chamber_idx in chamber_idxs])

#calculate product concentration by dividing every chamber intensity by the slope of the standard curve for that chamber
product_concentration = luminance_data / slopes[np.newaxis, :, np.newaxis]


In [10]:
#make numpy array of all button_quants with[ subtracted backgrounds:
button_quant_no_background = [] #we will soon turn this into a numpy array
for chamber_idx in chamber_idxs:
    next_button_quant = db_conn._json_dict['button_quant'][chamber_idx]['summed_button_BGsub_Button_Quant']
    button_quant_no_background.append(next_button_quant)
button_quant_no_background = np.array(button_quant_no_background)

# use eGFP standard curve to convert between button quant and eGFP concentration
enzyme_concentration = button_quant_no_background / EGFP_SLOPE    #in units of EGFP_SLOPE_CONC_UNITS
print('Enzyme concentration shape:', enzyme_concentration.shape)


Enzyme concentration shape: (1792,)


### Fit initial rates

In [11]:
###TODO:
# 1) ~~I think addings nans kills the line fitting. Fix at some point. (in line fitting code, so we can keep nans?)~~
#    Fixed? Appears like it's working properly.
# 2) We're using the time values for the first chamber for all chambers. 
#    In practice, they're sometimes off by 1 second, which should not affect results much. Perhaps change in the future.
# 3) Kinetics fails without substrate_conc, even though it says it's optional. Also prints an ugly array which we should disable.

import kinetics

#make an array of initial slopes for each chamber: should be (#chambers , #concentrations) = (1792 x 11)
initial_slopes = None
initial_slopes_R2 = None
for i, chamber_idx in enumerate(chamber_idxs):

    #use the kinetics package to calculate the slopes for this chamber at each substrate concentration.
    current_chamber_slopes, current_chamber_R2 = kinetics.get_initial_slopes(time_data[:,0], product_concentration[:,i,:].T, substrate_concs=conc_data)

    #add a dimension at the end:
    current_chamber_slopes = np.expand_dims(current_chamber_slopes, axis=0)
    current_chamber_R2 = np.expand_dims(current_chamber_R2, axis=0)
    
    #add to our complete array:
    if initial_slopes is None:
        initial_slopes = current_chamber_slopes
        initial_slopes_R2 = current_chamber_R2
    else:
        initial_slopes = np.concatenate([initial_slopes, current_chamber_slopes], axis=0)
        initial_slopes_R2 = np.concatenate([initial_slopes_R2, current_chamber_R2], axis=0)

 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to th

/home/nfreitas/workspace/pinney/kinetic_analysis/kinetics/functions.py:104: RuntimeWarning:

invalid value encountered in divide



 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to the data.
 This is likely due to scipy failing to fit a linear model to th

In [12]:
#Let's plot as before:
#plotting variable: We'll plot by luminance. We need a dictionary mapping chamber id (e.g. '1,1') to the value to be plotted (e.g. slope)
initial_rates_to_plot = {chamber_idxs[i]: np.nanmax(initial_slopes[i,:]) for i in range(len(chamber_idxs))}

#chamber_names: Same as before.

#plotting function: We'll generate a subplot for each chamber, showing the raw data and the linear regression line.
# to do this, we make a function that takes in the chamber_id and the axis object, and returns the axis object after plotting. Do NOT plot.show() in this function.
def plot_chamber_initial_rates(chamber_id, ax):
    #N.B. Every so often, slope and line colors don't match up. Not sure why.
    #parameters: what amount of total time to plot? First 20%?
    time_to_plot = 0.2
    
    #convert from 'x,y' to integer index in the array:
    data_index = list(chamber_idxs).index(chamber_id)

    x_data = time_data[:,0]
    y_data = product_concentration[:,data_index,:].T
    
    #plot only first X% of time:
    max_time = np.nanmax(x_data)
    time_to_plot = max_time*time_to_plot
    time_idxs_to_plot = x_data < time_to_plot
    x_data = x_data[time_idxs_to_plot]
    y_data = y_data[:, time_idxs_to_plot]
    
    #get slope from the analysis:
    current_chamber_slopes = initial_slopes[data_index,:]
    #calculate y-intercept by making sure it intersects first point:
    current_chamber_intercepts = y_data[:,0] - current_chamber_slopes*x_data[0] #note: not true y-intercept from linear regression
    
    for i in range(y_data.shape[0]): #over each concentration:
        ax.scatter(x_data, y_data[i,:])
        m = current_chamber_slopes[i]
        b = current_chamber_intercepts[i]
        if not (np.isnan(m) or np.isnan(b)):
            #return False, no_update, no_update
            ax.plot(x_data, m*np.array(x_data) + b)
    return ax


### PLOT THE CHIP: now, we plot
plot_chip(initial_rates_to_plot, chamber_names_dict, graphing_function=plot_chamber_initial_rates, title='Kinetics: Initial Rates (Max)')

/tmp/ipykernel_18032/663783430.py:3: RuntimeWarning:

All-NaN slice encountered



## 8. Filter initial rates

#### Filters:
We will filter by masking our product_concentration array with NaN values

In [13]:
### Filter threshholds ###

#standard curve r^2 threshhold:
r2_threshold = 0.98

#enzyme expression threshhold:
expression_threshhold = 1.5
expression_threshhold_units = 'nM'

#initial rate fit R^2 threshhold:
intitial_rate_R2_threshhold = 0.8

In [14]:
### Make filters ###

# STANDARD CURVE FILTER #
# overwrite all chambers (rows) with r^2 values below the threshold with NaNs:
filter_r2 = np.ones_like(initial_slopes)
r2_values = np.array([db_conn._json_dict['runs']['standard_0']['analyses']['linear_regression']['chambers'][chamber_idx]['r2'] for chamber_idx in chamber_idxs])
_count = 0
for i, chamber_idx in enumerate(chamber_idxs):
    if r2_values[i] < r2_threshold:
        _count +=1
        filter_r2[i, :] = np.nan
print('Pearson r^2 filter: {}/{} chambers pass'.format(len(chamber_idxs)-_count, len(chamber_idxs)))

# ENZYME EXPRESSION FILTER #
# overwrite all chambers (rows) with enzyme expression below the threshold with NaNs:
#Double check the expression units match the EGFP units:
assert expression_threshhold_units == EGFP_SLOPE_CONC_UNITS, 'Error, enzyme expression and EGFP standard curve units do not match!'
filter_enzyme_expression = np.ones_like(initial_slopes)
_count = 0
for i, chamber_idx in enumerate(chamber_idxs):
    if enzyme_concentration[i] < expression_threshhold:
        _count +=1
        filter_enzyme_expression[i,:] = np.nan
print('Enzyme expression filter: {}/{} chambers pass'.format(len(chamber_idxs)-_count, len(chamber_idxs)))

# INITIAL RATE FIT FILTER #
# overwrite just the assays per chamber (single values) with initial rate fit R^2 values below the threshold with NaNs:
filter_initial_rate_R2 = np.ones_like(initial_slopes)
_count = 0
for i, chamber_idx in enumerate(chamber_idxs):
    _chamber_count = 0
    for j in range(len(conc_data)):
        if initial_slopes_R2[i,j] < intitial_rate_R2_threshhold:
            _chamber_count +=1
            filter_initial_rate_R2[i,j] = np.nan
    if len(conc_data) - _chamber_count < 10:
        _count +=1
print('Initial Rate R^2 filter: {}/{} chambers pass with 10 or more slopes.'.format(len(chamber_idxs)-_count, len(chamber_idxs)))

# POSITIVE INITIAL SLOPE FILTER #
# overwrite just the assays per chamber (single values) with initial slopes below zero with NaNs:
filter_positive_initial_slope = np.ones_like(initial_slopes)
_count = 0
for i, chamber_idx in enumerate(chamber_idxs):
    _chamber_count = 0
    for j in range(len(conc_data)):
        if initial_slopes[i,j] < 0:
            _chamber_count +=1
            filter_positive_initial_slope[i,j] = np.nan
    if len(conc_data) - _chamber_count < 10:
        _count +=1
print('Positive Initial Slope filter: {}/{} chambers pass with 10 or more slopes.'.format(len(chamber_idxs)-_count, len(chamber_idxs)))


### manually flagged wells ###
#TODO: implement

### TODO: make visualization!


Pearson r^2 filter: 1792/1792 chambers pass
Enzyme expression filter: 603/1792 chambers pass
Initial Rate R^2 filter: 1792/1792 chambers pass with 10 or more slopes.
Positive Initial Slope filter: 1056/1792 chambers pass with 10 or more slopes.


In [15]:
### Filter data ###
#apply filters:
filters = [filter_r2, filter_enzyme_expression, filter_initial_rate_R2, filter_positive_initial_slope]

filtered_initial_slopes = deepcopy(initial_slopes)
for filter in filters: filtered_initial_slopes *= filter

In [16]:
# chamber_idxs, luminance_data, conc_data, time_data

#save filtered data to new analysis:
if 'analyses' not in db_conn._json_dict['runs']['kinetics_0'].keys():
    db_conn._json_dict['runs']['kinetics_0']['analyses'] = {}

#initialize the dictionary
db_conn._json_dict['runs']['kinetics_0']['analyses']['initial_slopes_filtered'] = {
        'filters': ['filter_r2', 'filter_enzyme_expression', 'filter_initial_rate_R2', 'filter_positive_initial_slope'],
        'filter_r2': r2_threshold,
        'filter_enzyme_expression': expression_threshhold,
        'filter_enzyme_expression_units': expression_threshhold_units,
        'filter_initial_rate_R2': intitial_rate_R2_threshhold,
        'filter_positive_initial_slope': True,
        'assays': {}} 

for i in range(len(conc_data)):
    db_conn._json_dict['runs']['kinetics_0']['analyses']['initial_slopes_filtered']['assays'][i] = {
        'substrate_conc': conc_data[i],
        'chambers': {}
    }
    for j, chamber_idx in enumerate(chamber_idxs):
        db_conn._json_dict['runs']['kinetics_0']['analyses']['initial_slopes_filtered']['assays'][i]['chambers'][chamber_idx] = {
            'slope': filtered_initial_slopes[j,i],
            'r2': initial_slopes_R2[j,i]
        }

In [17]:
###N.B.: May be some bug here, because some of the filtered-out chambers are still showing slopes.
# I think they should have all nans...?

#Let's plot as before:
#plotting variable: We'll plot by luminance. We need a dictionary mapping chamber id (e.g. '1,1') to the value to be plotted (e.g. slope)
filtered_initial_rates_to_plot = {chamber_idxs[i]: np.any(~np.isnan(filtered_initial_slopes[i,:])) for i in range(len(chamber_idxs))}

#chamber_names: Same as before.

#plotting function: We'll generate a subplot for each chamber, showing the raw data and the linear regression line.
# to do this, we make a function that takes in the chamber_id and the axis object, and returns the axis object after plotting. Do NOT plot.show() in this function.
def plot_chamber_filtered_initial_rates(chamber_id, ax):
    #N.B. Every so often, slope and line colors don't match up. Not sure why.
    #parameters: what amount of total time to plot? First 20%?
    time_to_plot = 0.2
    
    #convert from 'x,y' to integer index in the array:
    data_index = list(chamber_idxs).index(chamber_id)

    x_data = time_data[:,0]
    y_data = product_concentration[:,data_index,:].T
    
    #plot only first X% of time:
    max_time = np.nanmax(x_data)
    time_to_plot = max_time*time_to_plot
    time_idxs_to_plot = x_data < time_to_plot
    x_data = x_data[time_idxs_to_plot]
    y_data = y_data[:, time_idxs_to_plot]
    
    #get slope from the analysis:
    current_chamber_slopes = filtered_initial_slopes[data_index,:]
    #calculate y-intercept by making sure it intersects first point:
    current_chamber_intercepts = y_data[:,0] - current_chamber_slopes*x_data[0] #note: not true y-intercept from linear regression
    
    for i in range(y_data.shape[0]): #over each concentration:
        ax.scatter(x_data, y_data[i,:])
        m = current_chamber_slopes[i]
        b = current_chamber_intercepts[i]
        if not (np.isnan(m) or np.isnan(b)):
            #return False, no_update, no_update
            ax.plot(x_data, m*np.array(x_data) + b)
    return ax


### PLOT THE CHIP: now, we plot
plot_chip(filtered_initial_rates_to_plot, chamber_names_dict, graphing_function=plot_chamber_filtered_initial_rates, title='Kinetics: Filtered Initial Rates (Max)')
print('{}/1792 wells pass our filters.'.format( np.sum([x for x in filtered_initial_rates_to_plot.values()]) ) )

597/1792 wells pass our filters.


## 9. Fit Michalis-Menten curves and visualize

**Important!** We must match our units for enzyme concentration with substrate concentration! 

In [18]:
substrate_conc_unit = db_conn._json_dict['runs']['kinetics_0']['conc_unit']
if  substrate_conc_unit != EGFP_SLOPE_CONC_UNITS: print('Substrate concentration units do not match EGFP standard curve units! \n{} != {}'.format(substrate_conc_unit, EGFP_SLOPE_CONC_UNITS))

unit_converstion = 0.001 #convert FROM eGFP units TO substrate units (in this case, nM to uM)
enzyme_concentration_converted_units = enzyme_concentration * unit_converstion

#Double check!
print('Conversion:')
print('{} {} = {} {}  ?'.format(enzyme_concentration[0], EGFP_SLOPE_CONC_UNITS, enzyme_concentration_converted_units[0], substrate_conc_unit))


Substrate concentration units do not match EGFP standard curve units! 
uM != nM
Conversion:
0.9111313674217517 nM = 0.0009111313674217517 uM  ?


In [20]:
#Here, we calculate the Michaelis-Menten parameters for each chamber.

k_cat_array = np.array([])
k_cat_error_array = np.array([])
k_M_array = np.array([])
k_M_error_array = np.array([])

for i in range(len(chamber_idxs)):
    current_slopes = filtered_initial_slopes[i, :]

    if np.all(np.isnan(current_slopes)):
        print('Chamber {} has no slopes!'.format(chamber_idxs[i]))
        k_cat_array = np.append(k_cat_array, np.nan)
        k_cat_error_array = np.append(k_cat_error_array, np.nan)
        k_M_array = np.append(k_M_array, np.nan)
        k_M_error_array = np.append(k_M_error_array, np.nan)
        continue

    #get indices of non-nan values:
    non_nan_idxs = np.where(~np.isnan(current_slopes))[0]
    
    current_slopes = current_slopes[non_nan_idxs]
    current_concs = conc_data[non_nan_idxs]

    if len(current_slopes) < 3:
        print('Chamber {} has fewer than 3 slopes!'.format(chamber_idxs[i]))
        k_cat_array = np.append(k_cat_array, np.nan)
        k_cat_error_array = np.append(k_cat_error_array, np.nan)
        k_M_array = np.append(k_M_array, np.nan)
        k_M_error_array = np.append(k_M_error_array, np.nan)
        continue
    
    #kinetics.fit_and_plot_micheaelis_menten(current_slopes, current_slopes, current_concs, enzyme_concentration_converted_units[i], 'uM', 'MM for first chamber!')
    k_cat, k_M, std_err = kinetics.fit_michaelis_menten(current_slopes, current_slopes, current_concs, enzyme_concentration_converted_units[i], 'uM', 'MM for first chamber!')
    k_cat_array = np.append(k_cat_array, k_cat)
    k_cat_error_array = np.append(k_cat_error_array, std_err[0])
    k_M_array = np.append(k_M_array, k_M)
    k_M_error_array = np.append(k_M_error_array, std_err[1])

v_max_array = k_cat_array * enzyme_concentration_converted_units #in units of substrate_conc_unit
v_max_error_array = k_cat_error_array * enzyme_concentration_converted_units #in units of substrate_conc_unit

Chamber 1,1 has no slopes!
Chamber 1,2 has no slopes!
Chamber 1,3 has no slopes!
Chamber 1,4 has no slopes!
Chamber 1,5 has no slopes!
Chamber 1,6 has no slopes!
Chamber 1,7 has no slopes!
Chamber 1,8 has no slopes!
Chamber 1,9 has no slopes!
Chamber 1,10 has no slopes!
Chamber 1,11 has no slopes!
Chamber 1,12 has no slopes!
Chamber 1,14 has no slopes!
Chamber 1,15 has no slopes!
Chamber 1,16 has no slopes!
Chamber 1,18 has no slopes!
Chamber 1,19 has no slopes!
Chamber 1,20 has no slopes!
Chamber 1,21 has no slopes!
Chamber 1,22 has no slopes!
Chamber 1,23 has no slopes!
Chamber 1,24 has no slopes!
Chamber 1,25 has no slopes!
Chamber 1,26 has no slopes!
Chamber 1,27 has no slopes!
Chamber 1,28 has no slopes!
Chamber 1,29 has no slopes!
Chamber 1,30 has no slopes!
Chamber 1,31 has no slopes!
Chamber 1,32 has no slopes!
Chamber 1,33 has no slopes!
Chamber 1,34 has no slopes!
Chamber 1,35 has no slopes!
Chamber 1,37 has no slopes!
Chamber 1,39 has no slopes!
Chamber 1,40 has no slopes!
C

/home/nfreitas/miniconda3/envs/htbam_analysis/lib/python3.10/site-packages/scipy/optimize/_minpack_py.py:881: OptimizeWarning:

Covariance of the parameters could not be estimated



Now, we'll save the raw Michaelis Menten paremters to a new analysis in the DB

In [21]:
# chamber_idxs, luminance_data, conc_data, time_data

#save filtered data to new analysis:
if 'analyses' not in db_conn._json_dict['runs']['kinetics_0'].keys():
    db_conn._json_dict['runs']['kinetics_0']['analyses'] = {}

#initialize the dictionary
db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw'] = {
        'chambers': {}} 

for i, chamber_idx in enumerate(chamber_idxs):
    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx] = {
        'k_cat': k_cat_array[i],
        'k_cat_error': k_cat_error_array[i],
        'k_M': k_M_array[i],
        'k_M_error': k_M_error_array[i],
        'v_max': v_max_array[i],
        'v_max_error': v_max_error_array[i]
    }

Above, we've kept the Michaelis-Menten parameters grouped into their wells. Since we've run several replicates in different wells, we'll group them here by replicate, using the 'id' value:

In [22]:
#Get chamber ids from metadata:
chamber_name_to_idx = {}
for chamber_idx, subdict in db_conn._json_dict['chamber_metadata'].items():
    name = subdict['id']
    if name not in chamber_name_to_idx.keys():
        chamber_name_to_idx[name] = [chamber_idx]
    else:
        chamber_name_to_idx[name].append(chamber_idx)

#get average number of replicates:
n_replicates = np.mean([len(x) for x in chamber_name_to_idx.values()])
print('Average number of replicates per sample: {}'.format(np.round(n_replicates, 1)))

Average number of replicates per sample: 18.1


Here we gather and filter our MM-data. What z-score would we like to use to distinguish outliers?

In [23]:
z_score_threshhold_MM = 1.5
z_score_threshhold_expression = 1.5

In [24]:
#Get average k_cat, k_M, and v_max for each sample:
sample_names = np.array([])
sample_k_cat = np.array([])
sample_k_cat_error = np.array([])
sample_k_cat_replicates = []
sample_k_M = np.array([])           #in units of substrate_conc_unit
sample_k_M_error = np.array([])
sample_k_M_replicates = []
sample_v_max = np.array([])         #in units of substrate_conc_unit
sample_v_max_error = np.array([])
sample_v_max_replicates = []

#Get z-scores for each well (used to filter in the next step!)
k_cat_zscores = np.array([])
k_M_zscores = np.array([])
v_max_zscores = np.array([])
enzyme_concentration_zscores = np.array([])

#For each sample, 
for name, ids in chamber_name_to_idx.items():

    ### GATHER MM PARAMETERS OF REPLICATES FOR EACH SAMPLE: ###
    #get indices of idxs in chamber_idxs:
    idxs = [list(chamber_idxs).index(x) for x in ids]

    #get values for those indices:
    k_cat = k_cat_array[idxs]
    k_M = k_M_array[idxs]
    v_max = v_max_array[idxs]
    #keep track of which wells we exclude later:
    k_cat_replicates = np.array(ids)
    k_M_replicates = np.array(ids)
    v_max_replicates = np.array(ids)

    #if any of these is all nans, just continue to avoid errors:
    if np.all(np.isnan(k_cat)) or np.all(np.isnan(k_M)) or np.all(np.isnan(v_max)):
        print('No values from sample {}, all pre-filtered.'.format(name))
        continue

    ### FILTER OUT OUTLIERS: ###
    #calculate z-score for each value:
    k_cat_zscore = (k_cat - np.nanmean(k_cat))/np.nanstd(k_cat)
    k_M_zscore = (k_M - np.nanmean(k_M))/np.nanstd(k_M)
    v_max_zscore = (v_max - np.nanmean(v_max))/np.nanstd(v_max)
    #also, get z-score of enzyme expression for each well:
    enzyme_concentration_zscore = (enzyme_concentration_converted_units[idxs] - np.nanmean(enzyme_concentration_converted_units[idxs]))/np.nanstd(enzyme_concentration_converted_units[idxs]) #in units of 'substrate_conc_unit' 

    #First, for enzyme expression outliers, set the value to NaN to be filtered in the final step:
    k_cat[np.abs(enzyme_concentration_zscore) > z_score_threshhold_expression] = np.nan
    k_M[np.abs(enzyme_concentration_zscore) > z_score_threshhold_expression] = np.nan
    v_max[np.abs(enzyme_concentration_zscore) > z_score_threshhold_expression] = np.nan

    #filter out values with z-score > threshhold:
    k_cat = k_cat[np.abs(k_cat_zscore) < z_score_threshhold_MM]
    k_M = k_M[np.abs(k_M_zscore) < z_score_threshhold_MM]
    v_max = v_max[np.abs(v_max_zscore) < z_score_threshhold_MM]
    #do the same for the replicates ids:
    k_cat_replicates = k_cat_replicates[np.abs(k_cat_zscore) < z_score_threshhold_MM]
    k_M_replicates = k_M_replicates[np.abs(k_M_zscore) < z_score_threshhold_MM]
    v_max_replicates = v_max_replicates[np.abs(v_max_zscore) < z_score_threshhold_MM]

    #remove nan values from all (nan values are due to both no experimental data, and z-score filtering)
    k_cat_replicates = k_cat_replicates[~np.isnan(k_cat)]
    k_M_replicates = k_M_replicates[~np.isnan(k_M)]
    v_max_replicates = v_max_replicates[~np.isnan(v_max)]
    k_cat = k_cat[~np.isnan(k_cat)]
    k_M = k_M[~np.isnan(k_M)]
    v_max = v_max[~np.isnan(v_max)]

    if len(k_cat) < 3:
        print('Not enough replicates for sample {}. Skipping.'.format(name))
        continue
    
    #get average values:
    sample_names = np.append(sample_names, name)
    sample_k_cat = np.append(sample_k_cat, np.mean(k_cat))
    sample_k_cat_error = np.append(sample_k_cat_error,np.std(k_cat))
    sample_k_M = np.append(sample_k_M, np.mean(k_M))
    sample_k_M_error = np.append(sample_k_M_error, np.std(k_M))
    sample_v_max = np.append(sample_v_max, np.mean(v_max))
    sample_v_max_error = np.append(sample_v_max_error, np.std(v_max))
    #keep track of replicates:
    sample_k_cat_replicates.append(k_cat_replicates)
    sample_k_M_replicates.append(k_M_replicates)
    sample_v_max_replicates.append(v_max_replicates)



No values from sample P_syri_ADK, all pre-filtered.
No values from sample D_hafn_ADK, all pre-filtered.
No values from sample H_mode_ADK, all pre-filtered.
No values from sample L_lact_ADK, all pre-filtered.
No values from sample L_reut_ADK, all pre-filtered.
No values from sample G_diaz_ADK, all pre-filtered.
No values from sample B_hens_ADK, all pre-filtered.
No values from sample S_coel_ADK, all pre-filtered.
No values from sample A_medi_ADK, all pre-filtered.
No values from sample M_hydr_ADK, all pre-filtered.
No values from sample A_orem_ADK, all pre-filtered.
No values from sample G_kaus_ADK, all pre-filtered.
No values from sample T_sibi_ADK, all pre-filtered.
No values from sample T_yell_ADK, all pre-filtered.
No values from sample C_japo_ADK, all pre-filtered.
No values from sample M_burt_ADK, all pre-filtered.
Not enough replicates for sample A_deha_ADK. Skipping.
No values from sample C_trac_ADK, all pre-filtered.
No values from sample S_hali_ADK, all pre-filtered.
No values

/tmp/ipykernel_18032/2068473347.py:42: RuntimeWarning:

divide by zero encountered in divide

/tmp/ipykernel_18032/2068473347.py:42: RuntimeWarning:

invalid value encountered in divide

/tmp/ipykernel_18032/2068473347.py:43: RuntimeWarning:

divide by zero encountered in divide

/tmp/ipykernel_18032/2068473347.py:43: RuntimeWarning:

invalid value encountered in divide

/tmp/ipykernel_18032/2068473347.py:44: RuntimeWarning:

divide by zero encountered in divide

/tmp/ipykernel_18032/2068473347.py:44: RuntimeWarning:

invalid value encountered in divide



Now, we add this to the database:

In [25]:
#save filtered data to new analysis:
if 'analyses' not in db_conn._json_dict['runs']['kinetics_0'].keys():
    db_conn._json_dict['runs']['kinetics_0']['analyses'] = {}

#initialize the dictionary
db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_filtered'] = {
        'samples': {}} 

for i, sample_name in enumerate(sample_names):
    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_filtered']['samples'][sample_name] = {
        'k_cat': sample_k_cat[i],
        'k_cat_error': sample_k_cat_error[i],
        'k_cat_replicates': sample_k_cat_replicates[i],
        'k_M': sample_k_M[i],
        'k_M_error': sample_k_M_error[i],
        'k_M_replicates': sample_k_M_replicates[i],
        'v_max': sample_v_max[i],
        'v_max_error': sample_v_max_error[i],
        'v_max_replicates': sample_v_max_replicates[i]
    }

In [26]:
#visualize:
#plotting variable: We'll plot by K_M. We need a dictionary mapping chamber id (e.g. '1,1') to the value to be plotted
#first, fill it with NaNs as a placeholder:
k_M_to_plot = {chamber_idx: np.nan for chamber_idx in chamber_idxs}
#then, fill in the values we have:
for i in range(len(sample_names)):
    for chamber_idx in chamber_name_to_idx[sample_names[i]]:
        k_M_to_plot[chamber_idx] = sample_k_M[i]

#plotting function: We'll generate an MM subplot for each chamber.
def plot_chamber_MM(chamber_id, ax):
    #find the name of the chamber:
    chamber_name = chamber_names_dict[chamber_id]
    #first, find all chambers with this name:
    #if there's no data, just skip!
    if chamber_name not in db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_filtered']['samples']:
        return ax
    chamber_id_list = db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_filtered']['samples'][chamber_name]['k_M_replicates']

    #convert to array indices:
    chamber_id_list = [list(chamber_idxs).index(x) for x in chamber_id_list]

    #get the initial rates for each chamber:
    initial_slopes = filtered_initial_slopes[chamber_id_list,:]
    #get average
    initial_slopes_avg = np.nanmean(initial_slopes, axis=0)
    #get error bars
    initial_slopes_std = np.nanstd(initial_slopes, axis=0)

    #get the substrate concentrations that match with each initial rate:
    substrate_concs = conc_data

    x_data = substrate_concs
    y_data = initial_slopes_avg

    #plot with error bars:
    ax.errorbar(x_data, y_data, yerr=initial_slopes_std, fmt='o')
    
    return ax

#chamber_names: We'll provide the name of the sample in each chamber as well, in the same way:
chamber_names_dict = {chamber_idx: subdict['id'] for chamber_idx, subdict in db_conn._json_dict['chamber_metadata'].items()}

### PLOT THE CHIP: now, we plot
plot_chip(k_M_to_plot, chamber_names_dict, graphing_function=plot_chamber_MM, title='Filtered K_M')

/tmp/ipykernel_18032/2572663681.py:26: RuntimeWarning:

Mean of empty slice

/home/nfreitas/miniconda3/envs/htbam_analysis/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1879: RuntimeWarning:

Degrees of freedom <= 0 for slice.



In [27]:
#Idea: Once we have initial fit for KM, have a view that flags each well by substrate "coverage":
#that is, whether our experiment had 1/10th and 10x substrate concentration than Vmax

In [28]:
# In the future, add a way to include more metadata like optimal growth temperature and full organism name


## 10. Export to CSV in format people like

In [29]:
#Summary CSV, showing data for each SAMPLE:
output_csv_name = 'kinetics_summary'

import csv
with open(output_csv_name+'_short.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter=',')
    #write header:
    writer.writerow(['id', 
                     'substrate_name', 
                     'assay_type', 
                     'replicates', 
                     'kcat_mean_filtered', 
                     'kcat_stdev_filtered', 
                     'Km_mean_filtered', 
                     'Km_stdev_filtered', 
                     'enzyme', 
                     'vmax_mean_filtered', 
                     'vmax_stdev_filtered'])
    #write data:
    for i, sample_name in enumerate(sample_names):
        row = [sample_name,
               sample_name,
               db_conn._json_dict['runs']['kinetics_0']['type'], 
               len(sample_k_cat_replicates[i]), 
               sample_k_cat[i], 
               sample_k_cat_error[i], 
               sample_k_M[i], 
               sample_k_M_error[i], 
               enzyme_concentration_converted_units[i],
               sample_v_max[i], 
               sample_v_max_error[i]]
        writer.writerow(row)

In [30]:
#Full CSV, showing data for each CHAMBER:
import csv
with open('margaux_11_22_23_kinetics_summary.csv', 'w', newline='') as csvfile:
    writer = csv.writer(csvfile, delimiter=',')
    #write header:
    writer.writerow(['id', 
                     'x,y',
                     'substrate_name', 
                     'assay_type', 
                     'replicates', 
                     'kcat', 
                     'kcat_mean_filtered', 
                     'kcat_stdev_filtered', 
                     'Km', 
                     'Km_mean_filtered', 
                     'Km_stdev_filtered', 
                     'enzyme',
                     'vmax', 
                     'vmax_mean_filtered', 
                     'vmax_stdev_filtered'])
    #write data for each chamber:
    for i, chamber_idx in enumerate(chamber_idxs):
        sample_name = chamber_names_dict[chamber_idx]
        #get index in sample_names:
        if sample_name in sample_names:
            sample_idx = list(sample_names).index(sample_name)
            row = [chamber_names_dict[chamber_idx], #id
                    chamber_idx, #x,y
                    sample_name, #substrate_name
                    db_conn._json_dict['runs']['kinetics_0']['type'], #assay_type
                    len(sample_k_cat_replicates[sample_idx]), #replicates
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['k_cat'], #kcat
                    sample_k_cat[sample_idx], #kcat_mean_filtered
                    sample_k_cat_error[sample_idx], #kcat_stdev_filtered
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['k_M'], #Km
                    sample_k_M[sample_idx], #Km_mean_filtered
                    sample_k_M_error[sample_idx], #Km_stdev_filtered
                    enzyme_concentration_converted_units[i], #enzyme
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['v_max'], #vmax
                    sample_v_max[sample_idx], #vmax_mean_filtered
                    sample_v_max_error[sample_idx]] #vmax_stdev_filtered
        else:
            row = [chamber_names_dict[chamber_idx], #id
                    chamber_idx, #x,y
                    sample_name, #substrate_name
                    db_conn._json_dict['runs']['kinetics_0']['type'], #assay_type
                    'NaN', #replicates
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['k_cat'], #kcat
                    'NaN', #kcat_mean_filtered
                    'NaN', #kcat_stdev_filtered
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['k_M'], #Km
                    'NaN', #Km_mean_filtered
                    'NaN', #Km_stdev_filtered
                    enzyme_concentration_converted_units[i], #enzyme
                    db_conn._json_dict['runs']['kinetics_0']['analyses']['michaelis_menten_raw']['chambers'][chamber_idx]['v_max'], #vmax
                    'NaN', #vmax_mean_filtered
                    'NaN' #vmax_stdev_filtered
            ]
        
        writer.writerow(row)